# Подготовка

In [3]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
from tqdm import tqdm
from itertools import product
from collections import Counter, defaultdict
import scipy
import pickle

import lightgbm
from lightgbm import LGBMClassifier
import xgboost

from sklearn.ensemble import RandomForestClassifier, BaggingClassifier
from sklearn.svm import SVC
from sklearn.pipeline import make_pipeline
from sklearn.metrics import roc_auc_score, precision_score, recall_score, classification_report, accuracy_score, f1_score
from sklearn import preprocessing
from sklearn.preprocessing import scale, StandardScaler, LabelEncoder
from sklearn.model_selection import GridSearchCV, train_test_split, GroupKFold, StratifiedKFold

/home/parazit/anaconda3/lib/python3.9/site-packages/scipy/__init__.py:155: UserWarning: A NumPy version >=1.18.5 and <1.25.0 is required for this version of SciPy (detected version 1.25.2
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [4]:
PATH_FEATURES = 'Features/'
PATH_SAMPLE_IDS = 'sample_ids/'
PATH_DATA = 'data/'
PATH_REPORTS = "tuning/reports/"
PATH_CLASSIFICATORS = "tuning/classificators/"

meta_df=pd.read_csv(PATH_DATA+'data_table.tsv', sep='\t', index_col = 'refseq id')

In [5]:
future_sample_id_uncrossing = pickle.load(open(PATH_SAMPLE_IDS + 'uncrossing_sample.pkl', 'rb'))[0]
future_sample_id_rhab = pickle.load(open(PATH_SAMPLE_IDS + 'rhabdoviridae_sample.pkl', 'rb'))
future_sample_id_crossing = pickle.load(open(PATH_SAMPLE_IDS + 'crossing_sample.pkl', 'rb'))

# Список функций

In [6]:
def find_best_model(X, y, clf, param_grid):
    model = GridSearchCV(estimator = clf, param_grid = param_grid, cv=5, verbose=10, scoring="f1_weighted")
    model.fit(X,y)
    print('Best weighted f1-score of Grid search: {}'.format(model.best_score_))
    print("Best model parameters of Grid search: {}".format(model.best_params_))
    return model.best_estimator_

def svc_prep(data, y_class_h):
         
    classes, list_y = sorted(data[y_class_h].unique()), []
 
    y = np.array(data[y_class_h])
    pre = preprocessing.LabelEncoder()
    pre.fit(classes)  
    y_int = pre.transform(y)
    
    for i in range(len(data[y_class_h].unique())):
        list_y.append(np.array(y_int == i).astype(int))
    
    return(list_y, classes, y_int)

# Достают признаки из файлов

def get_data_pd(feature_set):
    X = pd.read_csv(PATH_FEATURES+feature_set[0]+'.csv', index_col=0)
    for feature in feature_set[1:]:
        X = X.join(pd.read_csv(PATH_FEATURES+feature+'.csv', index_col=0))
    return X

def create_feature_set(features, kmer_lists):
    feature_set = [f'{f}_{k}' for i,f in enumerate(features) for k in kmer_lists[i] ]
    return feature_set

def get_X_y(df_table, df_feature, gbac, y_class_h, data_type):
    
    if data_type == 'ranged': # Работает для последовательностей, разбитых на участик 250, 400, 800
        
        df_feature['refseq id'] = [''.join([x+'_' for x in k.split('_')[:-1]])[:-1] for k in list(df_feature.index)]
        df_feature = df_feature.reset_index(drop = True)
        df_table = df_table.loc[df_feature['refseq id']]
        df_table = df_table.reset_index(drop = True)
        
        
        test_sample = pd.DataFrame()
        for seq_id in gbac:
            tmp = df_feature[df_feature['refseq id'] == seq_id]
            test_sample = pd.concat([test_sample, tmp])
        
        y_test = list(df_table.loc[test_sample.index][y_class_h])
        train_sample = df_feature[~df_feature.isin(test_sample)].dropna()
        y_train = list(df_table.loc[train_sample.index][y_class_h])
        
        
        indices_test = test_sample.index.to_numpy()
        #indices_train = df_feature.loc[train_sample.index].to_numpy()
        indices_train = train_sample.index.to_numpy()
        
        y_test = np.array(y_test)
        y_train = np.array(y_train)
        X_test = test_sample.iloc[:, :-1].to_numpy()
        X_train = train_sample.iloc[:, :-1].to_numpy()
        
        print('X_test size:', len(X_test), 'X_train size:', len(X_train), 'y_test size:', len(y_test), 'y_train size:', len(y_train))
        return(X_test, X_train, y_test, y_train, indices_test, indices_train)  
    
    if data_type == 'full': # Работает для полных последовательностей
        
        df_feature['indices'] = range(len(df_feature))

        test_sample = df_feature.loc[gbac]
        y_test = list(df_table.loc[gbac][y_class_h])
        train_sample = df_feature[~df_feature.isin(test_sample)].dropna()
        y_train = list(df_table.loc[list(train_sample.index)][y_class_h])

        indices_test = test_sample['indices'].to_numpy()
        indices_train = df_feature.loc[train_sample.index]['indices'].to_numpy()

        y_test = np.array(y_test)
        y_train = np.array(y_train)
        X_test = test_sample.iloc[:, :-1].to_numpy()
        X_train = train_sample.iloc[:, :-1].to_numpy()

        print('X_test size:', len(X_test), 'X_train size:', len(X_train), 'y_test size:', len(y_test), 'y_train size:', len(y_train))
        return(X_test, X_train, y_test, y_train, indices_test, indices_train)  


# Отвевает за обучение классификаторов. С помощью переменной models можно задать как одну модель, так и несколько сразу
# Сохраняются в словарь в порядке, в котором модели указаны в переменной models

def calc_models(models, X_train, y_train, X_test, y_test, indices_test, indices_train, y_class_h, list_y, classes, y_int):
    
    classificators = []
    svc_classes = []
    cl_reps = [] 
    for el in models:
        
        if el == 'rf':
            
            param_grid = { 
                "n_estimators": [100, 250, 500],
                "max_features": ['auto', 'sqrt', 'log2'],
                "max_depth" : [3,5,10,12],
                #"n_jobs":[-1],
                "criterion" :['gini', 'entropy']
                
            }


            model = RandomForestClassifier(random_state=42)
            gridCV_model = find_best_model(X_train, y_train, model, param_grid)                              
            classificators.append(gridCV_model)
            y_pred = gridCV_model.predict(X_test)
            cl_reps.append(classification_report(y_test, y_pred, output_dict = True, zero_division=1))
            print(el, classification_report(y_test, y_pred))

        if el == 'lgbm':
            
            param_grid = { 
                "n_estimators": [250, 500, 1000],
                "num_leaves": [8, 12, 16, 24, 32],
                "max_depth":[-1],#,6,12],
                "reg_lambda":[0.1, 1, 10],
                "reg_alpha": [0, 0.01, 0.1],
                #"n_jobs":[-1],
                "learning_rate":[0.1, 0.01]
                
            }
                
            
            
            model = LGBMClassifier(random_state=42)
            gridCV_model = find_best_model(X_train, y_train, model, param_grid)                              
            classificators.append(gridCV_model)
            y_pred = gridCV_model.predict(X_test)
            cl_reps.append(classification_report(y_test, y_pred, output_dict = True, zero_division=1))
            print(el, classification_report(y_test, y_pred))
            
        if el == 'xgb':
            le = LabelEncoder()
            y_train, y_test = le.fit_transform(y_train), le.fit_transform(y_test)
            
            param_grid = { 
                "max_depth":[6,12,18],
                "lambda":[0.1, 1, 10],
                "alpha": [0, 0.01, 0.1],
                "n_estimators":[50, 100, 250, 500],
                #"n_jobs":[-1],
                "min_child_weight":[3, 7, 12]
            }
            
            model = xgboost.XGBClassifier(random_state=42, objective='multi:softprob', eval_metric='auc')
            gridCV_model = find_best_model(X_train, y_train, model, param_grid)
            classificators.append(gridCV_model)
            y_pred = gridCV_model.predict(X_test)    
            cl_reps.append(classification_report(y_test, y_pred, output_dict = True, target_names = classes, zero_division=1))
            print(el, classification_report(y_test, y_pred, target_names = classes, zero_division=1))
            
        if el == 'svc':

            param_grid = {
                "n_estimators":[10],
                "max_samples":[1.0 / 10],
                "base_estimator__C":[1,10,100,1000],
                "base_estimator__gamma":[1, 0.1, 0.001, 0.0001, 'auto'],
                "base_estimator__kernel":['linear','rbf']}


            svc_classificators = [] 
            scale = True
            
            y_proba = np.zeros(shape=indices_test.shape)
            for y_class, class_name in tqdm(zip(list_y, classes)):
                y_train = y_class[indices_train]
                y_test = y_class[indices_test]

                #if scale == True:
                gridCV_model = make_pipeline(StandardScaler(), GridSearchCV(BaggingClassifier(SVC(probability=True)),
                                                                            param_grid = param_grid, 
                                                                            cv=5,
                                                                            verbose=10,
                                                                            scoring="f1_weighted"))
                #else:
                    #model = SVC()
                    #gridCV_model = find_best_model(X_train, y_train, model, param_grid)
                
                gridCV_model.fit(X_train, y_train)    
                svc_classificators.append(gridCV_model)
                y_pred = gridCV_model.predict(X_test)
                y_proba = np.vstack((y_proba, gridCV_model.predict_proba(X_test)[:,1]))
                print(class_name)

                print(classification_report(y_test, y_pred, target_names = ['Others', class_name], zero_division=1))
                svc_classes.append(classification_report(y_test, y_pred, output_dict=True, target_names = ['Others', class_name], zero_division=1))
        
            classificators.append(svc_classificators)
            y_proba = y_proba[1:]
            y_proba = (y_proba/y_proba.sum(axis=0))


            y_pred_all = np.argmax(y_proba, axis=0)
            cl_reps.append(classification_report(y_int[indices_test], y_pred_all, output_dict = True, target_names = classes, zero_division=1))
            print('F1-score (weighted):', round(f1_score(y_int[indices_test], y_pred_all, average='weighted'), 2))
            print('F1-score (macro):', round(f1_score(y_int[indices_test], y_pred_all, average='macro'), 2))
    return(cl_reps, svc_classes, classificators)

In [7]:
def training(models, features_sets, sample_type, y_class_h, full_or_ranged, subseq_len = '', best = None):
    
    # Изменение путей исключительно внутри функции. Подготовка индексов для SVC
    
    fun_PATH_FEATURES = PATH_FEATURES
    fun_PATH_CLASSIFICATORS = PATH_CLASSIFICATORS
    fun_PATH_REPORTS = PATH_REPORTS
    BEST_NAME = ''

    
    if full_or_ranged == 'full':
        fun_PATH_FEATURES = PATH_FEATURES[:-1]
        list_y, classes, y_int = svc_prep(meta_df, y_class_h)
        fun_all_sets_names = all_sets_names
        fun_sole_sets_names = sole_sets_names
        
    if full_or_ranged == 'ranged':
        fun_PATH_FEATURES = PATH_FEATURES
        meta_df_ranged = pd.read_csv(PATH_DATA+'data_table_' + subseq_len + '.tsv', sep=',', index_col = 0)
        list_y, classes, y_int = svc_prep(meta_df_ranged, y_class_h)
        fun_all_sets_names = sets_all_ranged_names
        fun_sole_sets_names = sets_sole_ranged_names
      
    if best:
        fun_PATH_REPORTS = PATH_REPORTS+'best/'
        fun_PATH_CLASSIFICATORS = PATH_CLASSIFICATORS+'best/'
        fun_all_sets_names = best_sets_all_names
        fun_sole_sets_names = best_sets_sole_names
        BEST_NAME = '_best'
    
    
    all_classificators = {}
    all_clfs = {}
    svc_classes_clfs = {}
    
    # Выбираем список refseq id для тестовой выборки
    
    if sample_type == 'rhab':
        future_sample_id = future_sample_id_rhab
    if sample_type == 'crossing':
        future_sample_id = future_sample_id_crossing
    if sample_type == 'uncrossing':
        future_sample_id = future_sample_id_uncrossing
    
    if len(features_sets[0]) > 1: # если длина 1 призака > 1, то это all_sets (комбинации признаков)
        
        for fset in features_sets: # берём комбинацию признаков (fset)

            print(fset, 'Collecting data...')
            X_test, X_train, y_test, y_train, indices_test, indices_train = get_X_y(meta_df, pd.read_csv(fun_PATH_FEATURES+subseq_len+'/'+fset[0]+'.csv', index_col=0), future_sample_id, y_class_h, full_or_ranged) # Сделали начальные X и у по 1 признаку (fset[0]) из нашей комбинации 
            y_test, y_train = y_test.astype('str'), y_train.astype('str') 

            for feature in fset[1:]: # далее добавляем остальные признаки из комбинации (fset[1:])
                feature_df = pd.read_csv(fun_PATH_FEATURES+subseq_len+'/'+feature+'.csv', index_col=0)
                X_test_0, X_train_0, y_test_0, y_train_0, indices_test_0, indices_train_0 = get_X_y(meta_df, feature_df, future_sample_id, y_class_h, full_or_ranged)
                print('X_test length: '+ str(len(X_test_0)))
                X_test, X_train = np.hstack((X_test, X_test_0)), np.hstack((X_train, X_train_0))

            print('Data obtained. Calculating models')
            out = calc_models(models, X_train, y_train, X_test, y_test, indices_test, indices_train, y_class_h, list_y, classes, y_int) # Обучаем модели
            all_clfs[fun_all_sets_names[features_sets.index(fset)]], \
            svc_classes_clfs[fun_all_sets_names[features_sets.index(fset)]], \
            all_classificators[fun_all_sets_names[features_sets.index(fset)]] = out[0], out[1], out[2]
            
        pickle.dump(all_clfs, open(fun_PATH_REPORTS + full_or_ranged + '/' + sample_type + '/' + 'clfs_all_'+subseq_len+'_'+sample_type+BEST_NAME+'.pkl', 'wb'))
        pickle.dump(svc_classes_clfs, open(fun_PATH_REPORTS + full_or_ranged + '/' + sample_type + '/' + 'clfs_svc_classes_all_'+subseq_len+'_'+sample_type+BEST_NAME+'.pkl', 'wb'))
        pickle.dump(all_classificators, open(fun_PATH_CLASSIFICATORS + full_or_ranged + '/' + sample_type + '/' + 'classificators_all_'+subseq_len+'_'+sample_type+BEST_NAME+'.pkl', 'wb'))
    
    if len(features_sets[0]) == 1: # если длина первого призака = 1, то это sole_sets (одиночные признаки)
        
        for fset in features_sets:
    
            print(fset, 'Collecting data...')
            X_test, X_train, y_test, y_train, indices_test, indices_train = get_X_y(meta_df, pd.read_csv(fun_PATH_FEATURES+subseq_len+'/'+fset[0]+'.csv', index_col=0), future_sample_id, y_class_h, full_or_ranged) # Создаём X и y

            print('Data obtained. Calculating models')
            out = calc_models(models, X_train, y_train, X_test, y_test, indices_test, indices_train, y_class_h, list_y, classes, y_int) # Обучаем модели
            all_clfs[fun_sole_sets_names[features_sets.index(fset)]], \
            svc_classes_clfs[fun_sole_sets_names[features_sets.index(fset)]], \
            all_classificators[fun_sole_sets_names[features_sets.index(fset)]] = out[0], out[1], out[2]
            
        pickle.dump(all_clfs, open(fun_PATH_REPORTS + full_or_ranged +'/' + sample_type + '/' + 'clfs_sole_'+subseq_len+'_'+sample_type+BEST_NAME+'.pkl', 'wb'))
        pickle.dump(svc_classes_clfs, open(fun_PATH_REPORTS + full_or_ranged + '/' + sample_type + '/' + 'clfs_svc_classes_sole_'+subseq_len+'_'+sample_type+BEST_NAME+'.pkl', 'wb'))
        pickle.dump(all_classificators, open(fun_PATH_CLASSIFICATORS + full_or_ranged + '/' + sample_type + '/' + 'classificators_sole_'+subseq_len+'_'+sample_type+BEST_NAME+'.pkl', 'wb'))

# Признаки

In [10]:
all_sets = [create_feature_set(['AA'], [list(range(1,3,1))]),
            create_feature_set(['AA'], [list(range(1,4,1))]),
            #create_feature_set(['AA'], [list(range(1,5,1))]),
            create_feature_set(['DNA'], [list(range(1,3,1))]),
            create_feature_set(['DNA'], [list(range(1,4,1))]),
            create_feature_set(['DNA'], [list(range(1,5,1))]),
            create_feature_set(['DNA'], [list(range(1,6,1))]),
            create_feature_set(['DNA'], [list(range(1,7,1))]),
            create_feature_set(['DNA'], [list(range(1,8,1))]),
            #['ORF_30'], ['ORF_31'], ['ORF_32'],
            create_feature_set(['AA'], [[1,3]]),
            #create_feature_set(['AA'], [[2,4]]),
            create_feature_set(['DNA'], [[1,3,5]]),
            create_feature_set(['DNA'], [[3,5]]),
            create_feature_set(['DNA'], [[2,4,6]]),
            create_feature_set(['DNA'], [[3,5,7]]),
            create_feature_set(['DNA','AA'], [list(range(1,4,1)),list(range(1,3,1))]),
            create_feature_set(['DNA','AA'], [list(range(2,5,1)),list(range(1,3,1))])
            ]

all_sets_names = ['AA1-2',
                 'AA1-3',
                 #'AA1-4',
                 'RNA1-2', 
                 'RNA1-3', 
                 'RNA1-4', 
                 'RNA1-5', 
                 'RNA1-6', 
                 'RNA1-7',
                 #'ORF_3+0',
                 #'ORF_3+1',
                 #'ORF_3+2',
                 'AA1,3',
                 #'AA2,4',
                 'RNA1,3,5',
                 'RNA3,5',
                 'RNA2,4,6',
                 'RNA3,5,7',
                 'RNA1-3,AA1-2',
                 'RNA2-4,AA1-2'
                ]

sole_sets = [['DNA_1'],
             ['DNA_2'],
             ['DNA_3'],
             ['DNA_4'],
             ['DNA_5'],
             ['DNA_6'],
             ['DNA_7'],
             ['AA_1'],
             ['AA_2'],
             ['AA_3'],
             #['AA_4']
            ]

sole_sets_names = ['RNA_1',
                  'RNA_2',
                  'RNA_3',
                  'RNA_4',
                  'RNA_5',
                  'RNA_6',
                  'RNA_7',
                  'AA_1',
                  'AA_2',
                  'AA_3',
                  #'AA_4'
                  ]

best_sets_all = [create_feature_set(['DNA'], [list(range(1,4,1))]),
                 create_feature_set(['DNA'], [list(range(1,5,1))]),
                 create_feature_set(['DNA'], [list(range(1,6,1))]),
                 create_feature_set(['DNA'], [list(range(2,5,1))]),
                 create_feature_set(['DNA'], [list(range(2,6,1))]),
                 create_feature_set(['AA'], [[1,2]]),   
                 create_feature_set(['DNA'], [[1,3,5]]),
                 create_feature_set(['DNA'], [[3,5]]),
                 create_feature_set(['DNA','AA'], [list(range(1,4,1)),list(range(1,3,1))]),
                 create_feature_set(['DNA','AA'], [list(range(2,5,1)),list(range(1,3,1))])
                ]



best_sets_all_names = ['RNA1-3', 
                       'RNA1-4', 
                       'RNA1-5',
                       'RNA2-4',
                       'RNA2-5',
                       'AA1-2',                      
                       'RNA1,3,5',
                       'RNA3,5',
                       'RNA1-3,AA1-2',
                       'RNA2-4,AA1-2'
                      ]



best_sets_sole = [['DNA_2'],
                ['DNA_3'],
                ['DNA_4'],
                ['DNA_5']
               ]

best_sets_sole_names = ['RNA_2',
                      'RNA_3',
                      'RNA_4',
                      'RNA_5'
                        ]

In [11]:
all_sets_ranged = [#create_feature_set(['AA'], [list(range(1,3,1))]),
            #create_feature_set(['AA'], [list(range(1,4,1))]),
            #create_feature_set(['AA'], [list(range(1,5,1))]),
            create_feature_set(['DNA'], [list(range(1,3,1))]),
            create_feature_set(['DNA'], [list(range(1,4,1))]),
            create_feature_set(['DNA'], [list(range(1,5,1))]),
            create_feature_set(['DNA'], [list(range(1,6,1))]),
            create_feature_set(['DNA'], [list(range(1,7,1))]),
            #create_feature_set(['DNA'], [list(range(1,8,1))]),
            #['ORF_30'], ['ORF_31'], ['ORF_32'],
            #create_feature_set(['AA'], [[1,3]]),
            #create_feature_set(['AA'], [[2,4]]),
            create_feature_set(['DNA'], [[1,3,5]]),
            create_feature_set(['DNA'], [[3,5]]),
            create_feature_set(['DNA'], [[2,4,6]]),
            #create_feature_set(['DNA'], [[3,5,7]]),
            #create_feature_set(['DNA','AA'], [list(range(1,4,1)),list(range(1,3,1))])
            ]

all_sets_ranged_names = [#'AA1-2',
                 #'AA1-3',
                 #'AA1-4',
                 'RNA1-2', 
                 'RNA1-3', 
                 'RNA1-4', 
                 'RNA1-5', 
                 'RNA1-6', 
                 #'RNA1-7',
                 #'ORF_3+0',
                 #'ORF_3+1',
                 #'ORF_3+2',
                 #'AA1,3',
                 #'AA2,4',
                 'RNA1,3,5',
                 'RNA3,5',
                 'RNA2,4,6',
                 #'RNA3,5,7',
                 #'RNA1-3,AA1-2',

                ]

sole_sets_ranged = [['DNA_1'],
                     ['DNA_2'],
                     ['DNA_3'],
                     ['DNA_4'],
                     ['DNA_5'],
                     ['DNA_6'],
                     #['DNA_7'],
                     #['AA_1'],
                     #['AA_2'],
                     #['AA_3'],
                     #['AA_4']
                    ]

sole_sets_ranged_names = ['RNA_1',
                          'RNA_2',
                          'RNA_3',
                          'RNA_4',
                          'RNA_5',
                          'RNA_6',
                          #'RNA_7',
                          #'AA_1',
                          #'AA_2',
                          #'AA_3',
                          #'AA_4'
                         ]

# Crossing full

In [12]:
models = ['rf', 'lgbm', 'xgb', 'svc']
sample_type = ['rhab', 'crossing', 'uncrossing']

In [18]:
len(all_sets) == len(all_sets_names)

True

In [20]:
all_sets_names

['AA1-2',
 'AA1-3',
 'RNA1-2',
 'RNA1-3',
 'RNA1-4',
 'RNA1-5',
 'RNA1-6',
 'RNA1-7',
 'AA1,3',
 'RNA1,3,5',
 'RNA3,5',
 'RNA2,4,6',
 'RNA3,5,7',
 'RNA1-3,AA1-2',
 'RNA2-4,AA1-2']

In [ ]:
training(models, all_sets, 'crossing', 'host', 'full')

['AA_1', 'AA_2'] Collecting data...
X_test size: 346 X_train size: 1044 y_test size: 346 y_train size: 1044
X_test size: 346 X_train size: 1044 y_test size: 346 y_train size: 1044
X_test length: 346
Data obtained. Calculating models
Fitting 5 folds for each of 72 candidates, totalling 360 fits
[CV 1/5; 1/72] START criterion=gini, max_depth=3, max_features=auto, n_estimators=100
[CV 1/5; 1/72] END criterion=gini, max_depth=3, max_features=auto, n_estimators=100;, score=0.360 total time=   0.2s
[CV 2/5; 1/72] START criterion=gini, max_depth=3, max_features=auto, n_estimators=100
[CV 2/5; 1/72] END criterion=gini, max_depth=3, max_features=auto, n_estimators=100;, score=0.481 total time=   0.2s
[CV 3/5; 1/72] START criterion=gini, max_depth=3, max_features=auto, n_estimators=100
[CV 3/5; 1/72] END criterion=gini, max_depth=3, max_features=auto, n_estimators=100;, score=0.700 total time=   0.2s
[CV 4/5; 1/72] START criterion=gini, max_depth=3, max_features=auto, n_estimators=100
[CV 4/5; 1

[CV 5/5; 8/72] END criterion=gini, max_depth=3, max_features=log2, n_estimators=250;, score=0.435 total time=   0.3s
[CV 1/5; 9/72] START criterion=gini, max_depth=3, max_features=log2, n_estimators=500
[CV 1/5; 9/72] END criterion=gini, max_depth=3, max_features=log2, n_estimators=500;, score=0.341 total time=   0.7s
[CV 2/5; 9/72] START criterion=gini, max_depth=3, max_features=log2, n_estimators=500
[CV 2/5; 9/72] END criterion=gini, max_depth=3, max_features=log2, n_estimators=500;, score=0.453 total time=   0.7s
[CV 3/5; 9/72] START criterion=gini, max_depth=3, max_features=log2, n_estimators=500
[CV 3/5; 9/72] END criterion=gini, max_depth=3, max_features=log2, n_estimators=500;, score=0.706 total time=   0.7s
[CV 4/5; 9/72] START criterion=gini, max_depth=3, max_features=log2, n_estimators=500
[CV 4/5; 9/72] END criterion=gini, max_depth=3, max_features=log2, n_estimators=500;, score=0.606 total time=   0.7s
[CV 5/5; 9/72] START criterion=gini, max_depth=3, max_features=log2, n_

[CV 1/5; 17/72] END criterion=gini, max_depth=5, max_features=log2, n_estimators=250;, score=0.499 total time=   0.4s
[CV 2/5; 17/72] START criterion=gini, max_depth=5, max_features=log2, n_estimators=250
[CV 2/5; 17/72] END criterion=gini, max_depth=5, max_features=log2, n_estimators=250;, score=0.590 total time=   0.4s
[CV 3/5; 17/72] START criterion=gini, max_depth=5, max_features=log2, n_estimators=250
[CV 3/5; 17/72] END criterion=gini, max_depth=5, max_features=log2, n_estimators=250;, score=0.767 total time=   0.4s
[CV 4/5; 17/72] START criterion=gini, max_depth=5, max_features=log2, n_estimators=250
[CV 4/5; 17/72] END criterion=gini, max_depth=5, max_features=log2, n_estimators=250;, score=0.719 total time=   0.4s
[CV 5/5; 17/72] START criterion=gini, max_depth=5, max_features=log2, n_estimators=250
[CV 5/5; 17/72] END criterion=gini, max_depth=5, max_features=log2, n_estimators=250;, score=0.483 total time=   0.4s
[CV 1/5; 18/72] START criterion=gini, max_depth=5, max_feature

[CV 1/5; 25/72] END criterion=gini, max_depth=10, max_features=log2, n_estimators=100;, score=0.577 total time=   0.2s
[CV 2/5; 25/72] START criterion=gini, max_depth=10, max_features=log2, n_estimators=100
[CV 2/5; 25/72] END criterion=gini, max_depth=10, max_features=log2, n_estimators=100;, score=0.741 total time=   0.2s
[CV 3/5; 25/72] START criterion=gini, max_depth=10, max_features=log2, n_estimators=100
[CV 3/5; 25/72] END criterion=gini, max_depth=10, max_features=log2, n_estimators=100;, score=0.852 total time=   0.2s
[CV 4/5; 25/72] START criterion=gini, max_depth=10, max_features=log2, n_estimators=100
[CV 4/5; 25/72] END criterion=gini, max_depth=10, max_features=log2, n_estimators=100;, score=0.770 total time=   0.2s
[CV 5/5; 25/72] START criterion=gini, max_depth=10, max_features=log2, n_estimators=100
[CV 5/5; 25/72] END criterion=gini, max_depth=10, max_features=log2, n_estimators=100;, score=0.539 total time=   0.2s
[CV 1/5; 26/72] START criterion=gini, max_depth=10, m

[CV 1/5; 33/72] END criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500;, score=0.622 total time=   2.1s
[CV 2/5; 33/72] START criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500
[CV 2/5; 33/72] END criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500;, score=0.764 total time=   2.1s
[CV 3/5; 33/72] START criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500
[CV 3/5; 33/72] END criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500;, score=0.852 total time=   2.1s
[CV 4/5; 33/72] START criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500
[CV 4/5; 33/72] END criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500;, score=0.800 total time=   2.0s
[CV 5/5; 33/72] START criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500
[CV 5/5; 33/72] END criterion=gini, max_depth=12, max_features=sqrt, n_estimators=500;, score=0.506 total time=   2.0s
[CV 1/5; 34/72] START criterion=gini, max_depth=12, m

...

[CV 1/5; 41/72] END criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250;, score=0.641 total time=   2.6s
[CV 2/5; 41/72] START criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250
[CV 2/5; 41/72] END criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250;, score=0.747 total time=   2.6s
[CV 3/5; 41/72] START criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250
[CV 3/5; 41/72] END criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250;, score=0.832 total time=   2.5s
[CV 4/5; 41/72] START criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250
[CV 4/5; 41/72] END criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250;, score=0.751 total time=   2.5s
[CV 5/5; 41/72] START criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250
[CV 5/5; 41/72] END criterion=entropy, max_depth=3, max_features=sqrt, n_estimators=250;, score=0.801 total time=   2.5s
[CV 1/5; 42/72] START criterion=ent

[CV 5/5; 48/72] END criterion=entropy, max_depth=5, max_features=auto, n_estimators=500;, score=0.824 total time=   7.6s
[CV 1/5; 49/72] START criterion=entropy, max_depth=5, max_features=sqrt, n_estimators=100
[CV 1/5; 49/72] END criterion=entropy, max_depth=5, max_features=sqrt, n_estimators=100;, score=0.714 total time=   1.5s
[CV 2/5; 49/72] START criterion=entropy, max_depth=5, max_features=sqrt, n_estimators=100
[CV 2/5; 49/72] END criterion=entropy, max_depth=5, max_features=sqrt, n_estimators=100;, score=0.785 total time=   1.5s
[CV 3/5; 49/72] START criterion=entropy, max_depth=5, max_features=sqrt, n_estimators=100
[CV 3/5; 49/72] END criterion=entropy, max_depth=5, max_features=sqrt, n_estimators=100;, score=0.919 total time=   1.5s
[CV 4/5; 49/72] START criterion=entropy, max_depth=5, max_features=sqrt, n_estimators=100
[CV 4/5; 49/72] END criterion=entropy, max_depth=5, max_features=sqrt, n_estimators=100;, score=0.783 total time=   1.5s
[CV 5/5; 49/72] START criterion=ent

[CV 4/5; 56/72] END criterion=entropy, max_depth=10, max_features=auto, n_estimators=250;, score=0.807 total time=   4.6s
[CV 5/5; 56/72] START criterion=entropy, max_depth=10, max_features=auto, n_estimators=250
[CV 5/5; 56/72] END criterion=entropy, max_depth=10, max_features=auto, n_estimators=250;, score=0.862 total time=   4.7s
[CV 1/5; 57/72] START criterion=entropy, max_depth=10, max_features=auto, n_estimators=500
[CV 1/5; 57/72] END criterion=entropy, max_depth=10, max_features=auto, n_estimators=500;, score=0.788 total time=   9.2s
[CV 2/5; 57/72] START criterion=entropy, max_depth=10, max_features=auto, n_estimators=500
[CV 2/5; 57/72] END criterion=entropy, max_depth=10, max_features=auto, n_estimators=500;, score=0.858 total time=   9.4s
[CV 3/5; 57/72] START criterion=entropy, max_depth=10, max_features=auto, n_estimators=500
[CV 3/5; 57/72] END criterion=entropy, max_depth=10, max_features=auto, n_estimators=500;, score=0.914 total time=   9.3s
[CV 4/5; 57/72] START crit

[CV 3/5; 64/72] END criterion=entropy, max_depth=12, max_features=auto, n_estimators=100;, score=0.904 total time=   1.9s
[CV 4/5; 64/72] START criterion=entropy, max_depth=12, max_features=auto, n_estimators=100
[CV 4/5; 64/72] END criterion=entropy, max_depth=12, max_features=auto, n_estimators=100;, score=0.802 total time=   1.9s
[CV 5/5; 64/72] START criterion=entropy, max_depth=12, max_features=auto, n_estimators=100
[CV 5/5; 64/72] END criterion=entropy, max_depth=12, max_features=auto, n_estimators=100;, score=0.862 total time=   1.9s
[CV 1/5; 65/72] START criterion=entropy, max_depth=12, max_features=auto, n_estimators=250
[CV 1/5; 65/72] END criterion=entropy, max_depth=12, max_features=auto, n_estimators=250;, score=0.794 total time=   4.7s
[CV 2/5; 65/72] START criterion=entropy, max_depth=12, max_features=auto, n_estimators=250
[CV 2/5; 65/72] END criterion=entropy, max_depth=12, max_features=auto, n_estimators=250;, score=0.833 total time=   4.7s
[CV 3/5; 65/72] START crit

[CV 2/5; 72/72] END criterion=entropy, max_depth=12, max_features=log2, n_estimators=500;, score=0.812 total time=   2.1s
[CV 3/5; 72/72] START criterion=entropy, max_depth=12, max_features=log2, n_estimators=500
[CV 3/5; 72/72] END criterion=entropy, max_depth=12, max_features=log2, n_estimators=500;, score=0.904 total time=   2.1s
[CV 4/5; 72/72] START criterion=entropy, max_depth=12, max_features=log2, n_estimators=500
[CV 4/5; 72/72] END criterion=entropy, max_depth=12, max_features=log2, n_estimators=500;, score=0.790 total time=   2.1s
[CV 5/5; 72/72] START criterion=entropy, max_depth=12, max_features=log2, n_estimators=500
[CV 5/5; 72/72] END criterion=entropy, max_depth=12, max_features=log2, n_estimators=500;, score=0.848 total time=   2.1s
Best weighted f1-score of Grid search: 0.8486088046037576
Best model parameters of Grid search: {'criterion': 'entropy', 'max_depth': 10, 'max_features': 'auto', 'n_estimators': 500}
rf                precision    recall  f1-score   suppor